# hw 3
Всеволод Сущевский

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import gensim
import gensim.corpora as corpora
from gensim import models
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

import spacy
nlp = spacy.load('ru_core_news_sm')

## Используем полученный в ДЗ 2 корпус

In [3]:
small_df = pd.read_csv('C:\\Users\\wirze\\DataspellProjects\\nlp_tg_bot\\hw2\\small_data.csv')
small_df

Unnamed: 0  index                          link  \
0              0  30056  /Forum/Appeals/Details/30056   
1              1  30047  /Forum/Appeals/Details/30047   
2              2  30043  /Forum/Appeals/Details/30043   
3              3  30037  /Forum/Appeals/Details/30037   
4              4  30016  /Forum/Appeals/Details/30016   
...          ...    ...                           ...   
2145        2145  26658  /Forum/Appeals/Details/26658   
2146        2146  26654  /Forum/Appeals/Details/26654   
2147        2147  26652  /Forum/Appeals/Details/26652   
2148        2148  26651  /Forum/Appeals/Details/26651   
2149        2149  26649  /Forum/Appeals/Details/26649   

                                                heading  \
0                                 Заявление-разьяснение   
1                      Уклонение от исполнения договора   
2                       торговля подделкой красной икры   
3                         Вопрос о втором законопроекте   
4                                             Мошенники   
...                                                 ...   
2145                            Как отправить ПЦР тест?   
2146  Отказали в возврате денежных средств за неиспо...   
2147                 Мошеннические схемы ГАЗЭНЕРГОБАНКа   
2148  Сайт отказал в возврате средств за неиспользов...   
2149                 Питомник Экоплант - обман с ценами   

                                                message  
0     Прошу предоставить правовую информацию, на осн...  
1     Здравствуйте!  По договору розничной купли-про...  
2     здравствуйте, я Шагеева Ольга Владимировна, пр...  
3     Здравствуйте! В сети интернет увидела введение...  
4     Здравствуйте! Пожалуйста, примите меры ! https...  
...                                                 ...  
2145  Как и куда отправить ответ ПЦР-теста, если нет...  
2146  Здравствуйте! Сайт Zengram списали с моей карт...  
2147  Прошу помочь урегулировать вопрос по страховым...  
2148  Добрый день! Сегодня обнаружила, что вчера веч...  
2149  5 июня 2021 г. на сайте Питомника растений  "Э...  

[2150 rows x 5 columns]

In [4]:
messages = small_df['message'].to_list()
messages

['Прошу предоставить правовую информацию, на основании каких законов и правовых актов в Иркутской области, транспортные компании(в лице водителей, проводников, кондукторов, охранных органов и т. д.) не допускают в транспортные общественные средства передвижения наземным, воздушным, железнодорожным способом передвижения; магазины розничной и оптовой торговли не продают товары первой необходимости человеку-гражданину, без средств индивидуальной защиты(маски и перчатки). Прошу предоставить документы с гербовыми печатями и подписями ответственных лиц подписавших данные постановления.',
 'Здравствуйте!  По договору розничной купли-продажи и монтажу витражей от 11.09.2021 ИП Гончаров Егор Васильевич (ИНН 310261985893) не исполняет свой обязательства. При заключении договора был оговорен срок исполнения - 21 календарный день с даты заключения договора. Причины неисполнения не называет, конкретный срок исполнения договора не называет. Смс с просьбой указать срок выполнения обязательств осталас

In [5]:
docs = list(nlp.pipe(messages))
docs

[Прошу предоставить правовую информацию, на основании каких законов и правовых актов в Иркутской области, транспортные компании(в лице водителей, проводников, кондукторов, охранных органов и т. д.) не допускают в транспортные общественные средства передвижения наземным, воздушным, железнодорожным способом передвижения; магазины розничной и оптовой торговли не продают товары первой необходимости человеку-гражданину, без средств индивидуальной защиты(маски и перчатки). Прошу предоставить документы с гербовыми печатями и подписями ответственных лиц подписавших данные постановления.,
 Здравствуйте!  По договору розничной купли-продажи и монтажу витражей от 11.09.2021 ИП Гончаров Егор Васильевич (ИНН 310261985893) не исполняет свой обязательства. При заключении договора был оговорен срок исполнения - 21 календарный день с даты заключения договора. Причины неисполнения не называет, конкретный срок исполнения договора не называет. Смс с просьбой указать срок выполнения обязательств осталась б

In [12]:
docs_clean = []
for doc in docs:
    small_list = []
    for token in doc:
        if not token.is_stop and not token.is_punct \
                and not token.is_space and token.is_alpha and len(token) > 2:
            small_list.append(token.lemma_)
    docs_clean.append(small_list)
docs_clean

[['просить',
  'предоставить',
  'правовой',
  'информация',
  'основание',
  'какой',
  'закон',
  'правовой',
  'акт',
  'иркутский',
  'область',
  'транспортный',
  'лицо',
  'водитель',
  'проводник',
  'кондуктор',
  'охранный',
  'орган',
  'допускать',
  'транспортный',
  'общественный',
  'средство',
  'передвижение',
  'наземный',
  'воздушный',
  'железнодорожный',
  'способ',
  'передвижение',
  'магазин',
  'розничный',
  'оптовый',
  'торговля',
  'продавать',
  'товар',
  'первый',
  'необходимость',
  'человек',
  'гражданин',
  'без',
  'средство',
  'индивидуальный',
  'перчатка',
  'просить',
  'предоставить',
  'документ',
  'гербовый',
  'печать',
  'подпись',
  'ответственный',
  'лицо',
  'подписать',
  'данные',
  'постановление'],
 ['здравствовать',
  'договор',
  'розничный',
  'купля',
  'продажа',
  'монтажу',
  'витраж',
  'гончаров',
  'егор',
  'василиевич',
  'инн',
  'исполнять',
  'обязательство',
  'заключение',
  'договор',
  'оговорить',
  'срок',
 

In [13]:
bad_words = ["здравствовать", "добрый", "день"]
clean_text = [
    [word for word in document if word not in bad_words]
    for document in docs_clean
]
clean_text

[['просить',
  'предоставить',
  'правовой',
  'информация',
  'основание',
  'какой',
  'закон',
  'правовой',
  'акт',
  'иркутский',
  'область',
  'транспортный',
  'лицо',
  'водитель',
  'проводник',
  'кондуктор',
  'охранный',
  'орган',
  'допускать',
  'транспортный',
  'общественный',
  'средство',
  'передвижение',
  'наземный',
  'воздушный',
  'железнодорожный',
  'способ',
  'передвижение',
  'магазин',
  'розничный',
  'оптовый',
  'торговля',
  'продавать',
  'товар',
  'первый',
  'необходимость',
  'человек',
  'гражданин',
  'без',
  'средство',
  'индивидуальный',
  'перчатка',
  'просить',
  'предоставить',
  'документ',
  'гербовый',
  'печать',
  'подпись',
  'ответственный',
  'лицо',
  'подписать',
  'данные',
  'постановление'],
 ['договор',
  'розничный',
  'купля',
  'продажа',
  'монтажу',
  'витраж',
  'гончаров',
  'егор',
  'василиевич',
  'инн',
  'исполнять',
  'обязательство',
  'заключение',
  'договор',
  'оговорить',
  'срок',
  'исполнение',
  'к

In [14]:
#  создаем словарь
dictionary = corpora.Dictionary(clean_text)
# проводим векторизацию
corpus = [dictionary.doc2bow(text) for text in clean_text]
# # tfidf model
tfidf_model = models.TfidfModel(corpus)
# # tfidf
tfidf = tfidf_model[corpus]

In [15]:
lda_model = models.LdaMulticore(tfidf, num_topics=5, id2word=dictionary)
lda_model.print_topics(num_words=10)

[(0,
  '0.002*"товар" + 0.002*"магазин" + 0.002*"заказ" + 0.001*"тест" + 0.001*"возврат" + 0.001*"деньга" + 0.001*"банк" + 0.001*"ребёнок" + 0.001*"просить" + 0.001*"услуга"'),
 (1,
  '0.002*"магазин" + 0.001*"товар" + 0.001*"тест" + 0.001*"россия" + 0.001*"год" + 0.001*"без" + 0.001*"нужный" + 0.001*"продавец" + 0.001*"ребёнок" + 0.001*"сказать"'),
 (2,
  '0.002*"магазин" + 0.002*"товар" + 0.002*"тест" + 0.001*"деньга" + 0.001*"какой" + 0.001*"пцр" + 0.001*"вернуть" + 0.001*"возврат" + 0.001*"дом" + 0.001*"средство"'),
 (3,
  '0.003*"тест" + 0.002*"товар" + 0.002*"пцр" + 0.002*"нужный" + 0.002*"сдавать" + 0.002*"магазин" + 0.002*"заказ" + 0.001*"абхазия" + 0.001*"телефон" + 0.001*"вернуть"'),
 (4,
  '0.002*"магазин" + 0.001*"тест" + 0.001*"нужный" + 0.001*"товар" + 0.001*"ребёнок" + 0.001*"возврат" + 0.001*"деньга" + 0.001*"дом" + 0.001*"пцр" + 0.001*"заказ"')]

In [16]:
doc_topics = {}
i = 0
for d in clean_text:
    bow = dictionary.doc2bow(d)
    t = lda_model.get_document_topics(bow)
    doc_topics[i] = t
    i+=1

In [24]:
doc_topic = {}
for doc in doc_topics:
    stats = dict(doc_topics[doc])
    doc_topic[doc] = max(stats, key=stats.get)

## Векторизовать с помощью tf-idf

In [29]:
all_topics_csr = gensim.matutils.corpus2csc(tfidf)
all_topics_numpy = all_topics_csr.T.toarray()
all_topics_df = pd.DataFrame(all_topics_numpy, columns = list(range(0, 13791)))
all_topics_df

0         1         2         3         4         5         6      \
0     0.098368  0.054613  0.121675  0.179063  0.218548  0.077598  0.098790   
1     0.000000  0.058688  0.000000  0.000000  0.000000  0.000000  0.000000   
2     0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
3     0.000000  0.054507  0.000000  0.000000  0.000000  0.000000  0.000000   
4     0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
...        ...       ...       ...       ...       ...       ...       ...   
2145  0.000000  0.171687  0.000000  0.000000  0.000000  0.000000  0.000000   
2146  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2147  0.000000  0.038220  0.000000  0.000000  0.000000  0.000000  0.023045   
2148  0.000000  0.088720  0.000000  0.000000  0.000000  0.000000  0.000000   
2149  0.000000  0.013589  0.000000  0.000000  0.000000  0.000000  0.000000   

         7         8         9      ...     13781     13782     13783  \
0     0.076801  0.159321  0.159321  ...  0.000000  0.000000  0.000000   
1     0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
2     0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
3     0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
4     0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
...        ...       ...       ...  ...       ...       ...       ...   
2145  0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
2146  0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
2147  0.107495  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
2148  0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000   
2149  0.000000  0.000000  0.000000  ...  0.108757  0.108757  0.054378   

         13784     13785     13786     13787     13788     13789     13790  
0     0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
1     0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
2     0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
3     0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
4     0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
...        ...       ...       ...       ...       ...       ...       ...  
2145  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
2146  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
2147  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
2148  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  
2149  0.108757  0.054378  0.054378  0.108757  0.054378  0.054378  0.271892  

[2150 rows x 13791 columns]

In [25]:
pd.DataFrame.from_dict(doc_topic, orient='index', columns=['topic_lda'])

topic_lda
0             4
1             0
2             1
3             2
4             0
...         ...
2145          3
2146          0
2147          3
2148          0
2149          4

[2150 rows x 1 columns]

## Векторизовать с помощью word2vec

In [22]:
docs_vectors = {}
i = 0
for doc in docs:
    docs_vectors[i]= doc.vector
    i+=1

In [26]:
pd.DataFrame.from_dict(docs_vectors, orient='index')

0         1         2         3         4         5         6   \
0     0.035767  0.384336  0.113021 -0.202715 -0.055330  0.136802 -0.481523   
1     0.436687  0.407885  0.038504  0.124501  0.074468 -0.089575 -0.327122   
2     0.086568  0.228286  0.096585  0.265846  0.365482  0.120465 -0.212707   
3     0.146931  0.112485  0.145218 -0.000700  0.238037  0.313843 -0.254853   
4    -0.105389 -0.110853  0.190084 -0.215008  0.178835  0.244156 -0.225990   
...        ...       ...       ...       ...       ...       ...       ...   
2145 -0.266528  0.051856  0.610543  0.021875 -0.060008  0.206139 -0.604572   
2146  0.293651  0.160196 -0.024241 -0.016753  0.391876  0.138857 -0.249896   
2147  0.296447  0.229798 -0.017127  0.042531  0.223005  0.190568 -0.244645   
2148  0.271989  0.233674  0.029390  0.127245  0.389284  0.279144 -0.176608   
2149  0.225370 -0.207153  0.072895  0.588440  0.025490 -0.250150 -0.259392   

            7         8         9   ...        86        87        88  \
0     0.038582  0.032304 -0.234038  ... -0.207936 -0.186672 -0.203252   
1     0.378077 -0.101318 -0.439873  ...  0.369781 -0.486437 -0.140183   
2     0.332602  0.277923  0.079669  ...  0.045095 -0.504291 -0.471202   
3     0.225381  0.050331 -0.032691  ... -0.026776 -0.063773 -0.048865   
4     0.350201 -0.263572 -0.001874  ...  0.031847 -0.219135  0.153851   
...        ...       ...       ...  ...       ...       ...       ...   
2145  0.297991 -0.449788 -0.054923  ... -0.284378 -0.375209 -0.238282   
2146  0.341816  0.039873 -0.024689  ...  0.163150 -0.276187 -0.093926   
2147  0.249258  0.070684 -0.105984  ...  0.053326 -0.285305 -0.188436   
2148  0.430327  0.104280 -0.168413  ...  0.250178 -0.296202 -0.102081   
2149  0.269268  0.316449  0.219000  ... -0.262799 -0.108679  0.146981   

            89        90        91        92        93        94        95  
0     0.069480  0.024004  0.093715  0.055362  0.536141 -0.463554 -0.150550  
1     0.481907 -0.086317  0.245301  0.087253  0.391215  0.139046 -0.321870  
2     0.161937 -0.084368  0.445232 -0.058481  0.011919  0.188654  0.079889  
3     0.154270 -0.145141  0.069402 -0.007763  0.018111  0.347598  0.051352  
4    -0.286571 -0.173400 -0.199926 -0.344285  0.013479 -0.007358  0.273678  
...        ...       ...       ...       ...       ...       ...       ...  
2145 -0.306639 -0.432586  0.369701 -0.218126  0.580721  0.482210  0.287265  
2146  0.191911  0.028587 -0.057901 -0.286761  0.108526  0.468113  0.090649  
2147  0.189278 -0.161711  0.054643  0.081077  0.145180  0.173280 -0.172890  
2148  0.076511 -0.124482 -0.096365 -0.180381 -0.111483  0.447082 -0.037339  
2149 -0.153801 -0.248452  0.440309  0.209855  0.057023  0.174927  0.289068  

[2150 rows x 96 columns]